<a href="https://colab.research.google.com/github/franziskaMai/DynaSlot/blob/master/DynaSlot.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install -q git+https://github.com/svenschultze/Colab-live-figures

In [2]:
  !git clone https://github.com/franziskaMai/DynaSlot

fatal: destination path 'DynaSlot' already exists and is not an empty directory.


In [3]:
import matplotlib.pyplot as plt
import numpy as np
import matplotlib.ticker as ticker
from datetime import datetime as dt
from itertools import chain, permutations
import json 
import pandas as pd
import random
import math
import live

In [4]:
pd.set_option('mode.chained_assignment', None)

Zu Beginn werden die Zeitfensteranfragen und die Ereignisse aus dem Repository als JSON Datein geladen und eingelesen.

In [5]:
with open("DynaSlot/start_lager.json") as file:
    problem = json.load(file)
with open("DynaSlot/ereignisse.json") as file2:
    events = json.load(file2)

Für die einzelnen Ereignisse werden mithilfe vom Pandas Framework Tabellen erstellt und mit den übergebenen Daten befüllt. Außerdem werden die Daten für die Zeitfensteranfragen in eine seperate Tabelle abgespeichert.

In [6]:
orders = pd.DataFrame(problem["orders"], index= [x for x in range(len(problem["orders"]))])
added_ramps = pd.DataFrame(events["add_ramp"])
deleted_ramps = pd.DataFrame(events["delete_ramp"])
added_slots = pd.DataFrame(events["add_slot"])
deleted_slots = pd.DataFrame(events["delete_slot"])
delayed_slots = pd.DataFrame(events["delay_slot"])
maintainance = pd.DataFrame(events["maintainance"])
events = pd.DataFrame()

Eine erste Darstellung der Zeitfensteranfragen. Zuerst gibt es eine Anfragen id die automatisch generiert wird, dann die Transportfahrzeug **id**, den Zeitpunkt der Ankunft **timestamp** und die Dauer des Aufenthalts **duration**.



In [7]:
orders

id            timestamp duration
0   1  2020-07-27_08:30:20    01:00
1   0  2020-07-27_10:00:20    01:30
2   2  2020-07-27_10:00:20    02:00
3   3  2020-07-27_10:45:20    01:45
4   4  2020-07-27_10:00:20    01:22
5   5  2020-07-27_11:45:20    02:10
6   6  2020-07-27_12:45:20    01:30

Eine Funktion die aus einem Zeit-String die genaue Sekunden Anzahl berechnet. Beispielsweise wird eine Stunde zu 3600 Sekunden verrechnet. Diese Funktion wird für die Berechnung der **duration** benötigt

In [8]:
def get_sec(time_str):
    h, m = time_str.split(':')
    return int(h) * 3600 + int(m) * 60

Hier werden die zuvor eingelesenen Zeitfensteranfragen verarbeitet und in die Zeitfenster-Tabelle abgespeichert. **Timestamp** und **duration** werden zu Sekunden umgerechnet.

In [9]:
def preprocess(orders, number_of_ramps):
    orders = orders.copy(deep=True)

    orders["timestamp"] = pd.to_datetime(orders["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    orders["timestamp"] = orders["timestamp"].map(lambda t: t.timestamp())
    orders["desired_timestamp"] = orders["timestamp"]
    orders["duration"] = orders["duration"].map(lambda t: get_sec(t))
    orders["endtimes"] = orders["timestamp"] + orders["duration"]
    orders["ramp"] =  np.random.randint(1, number_of_ramps, size= len(orders))
    orders["slot_id"] = np.arange(len(orders.index))

    return orders

Im Folgenden werden die Ereignisse einzeln verarbeitet, sodass sie später im Programm genutzt werden können.

In [10]:
def preprocess_added_ramps(added_ramps):
    added_ramps = added_ramps.copy(deep=True)

    added_ramps["timestamp"] = pd.to_datetime(added_ramps["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    added_ramps["timestamp"] = added_ramps["timestamp"].map(lambda t: t.timestamp())

    return added_ramps

In [11]:
def preprocess_deleted_ramps(deleted_ramps):
    deleted_ramps = deleted_ramps.copy(deep=True)

    deleted_ramps["timestamp"] = pd.to_datetime(deleted_ramps["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    deleted_ramps["timestamp"] = deleted_ramps["timestamp"].map(lambda t: t.timestamp())    

    return deleted_ramps

In [12]:
def preprocess_added_slots(added_slots):
    added_slots = added_slots.copy(deep=True)

    added_slots["timestamp"] = pd.to_datetime(added_slots["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    added_slots["timestamp"] = added_slots["timestamp"].map(lambda t: t.timestamp())
    added_slots["timestamp_slot"] = pd.to_datetime(added_slots["timestamp_slot"], format="%Y-%m-%d_%H:%M:%S")
    added_slots["timestamp_slot"] = added_slots["timestamp_slot"].map(lambda t: t.timestamp())
    added_slots["duration"] = added_slots["duration"].map(lambda t: get_sec(t))
    added_slots["endtimes"] = added_slots["timestamp_slot"] + added_slots["duration"]

    return added_slots

In [13]:
def preprocess_deleted_slots(deleted_slots):
    deleted_slots = deleted_slots.copy(deep=True)

    deleted_slots["timestamp"] = pd.to_datetime(deleted_slots["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    deleted_slots["timestamp"] = deleted_slots["timestamp"].map(lambda t: t.timestamp())

    return deleted_slots

In [14]:
def preprocess_delayed_slots(delayed_slots):
    delayed_slots = delayed_slots.copy(deep=True)

    delayed_slots["timestamp"] = pd.to_datetime(delayed_slots["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    delayed_slots["timestamp"] = delayed_slots["timestamp"].map(lambda t: t.timestamp())
    delayed_slots["delay"] = delayed_slots["delay"].map(lambda t: get_sec(t))

    return delayed_slots

In [15]:
def preprocess_maintainance(maintainance):
    maintainance = maintainance.copy(deep=True)
    
    maintainance["timestamp"] = pd.to_datetime(maintainance["timestamp"], format="%Y-%m-%d_%H:%M:%S")
    maintainance["timestamp"] = maintainance["timestamp"].map(lambda t: t.timestamp())    
    maintainance["timestamp_slot"] = pd.to_datetime(maintainance["timestamp_slot"], format="%Y-%m-%d_%H:%M:%S")
    maintainance["timestamp_slot"] = maintainance["timestamp_slot"].map(lambda t: t.timestamp())    
    maintainance["duration"] = maintainance["duration"].map(lambda t: get_sec(t))
    maintainance["endtimes"] = maintainance["timestamp_slot"] + maintainance["duration"]

    return maintainance

Die Funktionen für die Vorbereitung der Daten werden aufgerufen und abgespeichert.

In [16]:
preprocessed_added_ramps = preprocess_added_ramps(added_ramps)
preprocessed_added_slots = preprocess_added_slots(added_slots)
preprocessed_deleted_ramps = preprocess_deleted_ramps(deleted_ramps)
preprocessed_deleted_slots = preprocess_deleted_slots(deleted_slots)
preprocessed_delayed_slots = preprocess_delayed_slots(delayed_slots)
preprocessed_maintainance = preprocess_maintainance(maintainance)

Alle Zeitstempel der Ereignisse sowie die Ereignisart **type** werden einer Event Tabelle hinzugefügt und angezeigt. Diese Tabelle wird im weiteren Verlauf zum Ausfüren der Ereignis in der richtigen Reihenfolge benötigt, momentan muss jedoch zuerst der Plan erstellt werden.

In [17]:
timestamp_list = []
event_type_list = []

timestamp_list.extend(preprocessed_added_slots["timestamp"])
timestamp_list.extend(preprocessed_deleted_slots["timestamp"])
timestamp_list.extend(preprocessed_added_ramps["timestamp"])
timestamp_list.extend(preprocessed_deleted_ramps["timestamp"])
timestamp_list.extend(preprocessed_delayed_slots["timestamp"])
timestamp_list.extend(preprocessed_maintainance["timestamp"])

event_type_list.extend(preprocessed_added_slots["type"])
event_type_list.extend(preprocessed_deleted_slots["type"])
event_type_list.extend(preprocessed_added_ramps["type"])
event_type_list.extend(preprocessed_deleted_ramps["type"])
event_type_list.extend(preprocessed_delayed_slots["type"])
event_type_list.extend(preprocessed_maintainance["type"])

events["timestamp"] = timestamp_list
events["type"] = event_type_list

events = events.sort_values(by=['timestamp'])
events

timestamp          type
4  1.595832e+09    delay_slot
2  1.595844e+09      add_ramp
5  1.595854e+09    delay_slot
3  1.595861e+09   delete_ramp
0  1.595930e+09      add_slot
6  1.595938e+09  maintainance
1  1.595945e+09   delete_slot

Zwei Funktionen für die Planerstellung. *max_overlap_in_ramp* überprüft für die übergebene Rampe, ob es für das gewünschte Zeitfenster Überschneidungen auf der Rampe gibt oder ob die Rampe vielleicht schon gelöscht wurde. Für die Überprüfung von Überschneidungen wird die Funktion *slot_overlap* aufgerufen, um jedes bereits verbuchte Zeitfenster mit dem neuen zu vergleichen und zu berechnen, wie stark sie sich überschneiden. Eine Liste mit den Überschneidungen auf der Rampe wird zurück an die aufrufende Funktion gegeben.

In [18]:
def slot_overlap(slot1, slot2): 
    if slot1["slot_id"] == slot2["slot_id"]:
        return -600
    return min(slot1["endtimes"], slot2["endtimes"]) - max(slot1["timestamp"], slot2["timestamp"])

def max_overlap_in_ramp(order, schedule, ramp):
    if ramp in deleted_ramps:
        return np.inf
    
    slots_for_ramp = schedule.loc[schedule["ramp"] == ramp]
    if slots_for_ramp.empty:
        return -600

    overlaps = [slot_overlap(slot, order) for _, slot in slots_for_ramp.iterrows()]
    return max(overlaps)

*Delay_fit* ist für die Erstellung des Plans zuständig. In dieser Funktion werden alle Anfragen durchlaufen, hier **orders** genannt. Dann wird die zuvor genannte Funktion *max_overlaps_in_ramp* für jede Rampe einmal aufgerufen, um eine Liste der Überschneidungen auf allen Rampen zu erhalten. Dann wird die Rampe bestimmt bei *best_ramp*, wo sich das Wunschzeitfenster und die bereits verplanten Zeitfenster am wenigsten überschneiden. Auf der besten Rampe wird dann das Zeitfenster solange verschoben, bis es eine freie Stelle im Plan gibt.

In [19]:
def delay_fit(orders, number_of_ramps):
    schedule = orders.iloc[0:0].copy(deep=True)
    for i in range(len(orders)):     
        order = orders.iloc[i]

        ramp_overlaps = [max_overlap_in_ramp(order, schedule, ramp) for ramp in range(number_of_ramps)]
        best_ramp = np.random.choice(np.argwhere(np.array(ramp_overlaps) == np.array(ramp_overlaps).min())[0])
   
        order["ramp"] = best_ramp

        while max_overlap_in_ramp(order, schedule, best_ramp) > 0:
            overlap = max_overlap_in_ramp(order, schedule, best_ramp)      
            order["timestamp"] += overlap + 600
            order["endtimes"] = order["timestamp"] + order["duration"]

        schedule = schedule.append(order)
        yield schedule

Überprüft ob Zeitfenster sich im aktuellen Plan überschneiden. Gibt einen Boolean zurück.

In [20]:
def is_overlapping(solution):
    for ramp in solution["ramp"].unique():
        slots = solution.loc[solution["ramp"] == ramp]
        sorted = slots.sort_values("timestamp")
        for i in range(len(sorted.index) - 1):
            if slot_overlap(sorted.iloc[i], sorted.iloc[i + 1]) > 0:
                return True 
    return False

Berechnet die Differenz zwischen gewünschtem und erhaltenem Zeitfenster (Zielfunktion). Überprüft auch, ob eine erstellte Lösung gültig ist durch den Aufruf von *is_overlapping*.

In [21]:
def fitness(x, schedule, preprocessed_orders):
    solution = decode(x, schedule)

    if is_overlapping(solution):
        return np.inf

    scores = [slot["timestamp"] - slot["desired_timestamp"] for i, slot in solution.iterrows()]
    scores = np.abs(scores)
    return sum(scores)

Enkodiert den Zeitplan, sodass schnell neue Lösungen generiert werden können. In *decode* werden die erstellten Lösungen wieder in Tabellenform gebracht.

In [22]:
def encode(schedule):
    encoded = [[slot["timestamp"], slot["ramp"]] for _, slot in schedule.iterrows()]
    return np.array(encoded)

def decode(encoded, schedule):
    new_schedule = schedule.copy(deep=True)
    for i in range(len(encoded)):
        new_schedule.loc[i, "timestamp"] = encoded[i][0]
        new_schedule.loc[i, "endtimes"] = encoded[i][0] + new_schedule.loc[i, "duration"]
        new_schedule.loc[i, "ramp"] = encoded[i][1]
    
    return new_schedule

Verändert den Plan durch das Anpassen von Rampen (zeitliche Verschiebung bzw. Verschiebung der Rampen). 

In [23]:
def mutation(x):
    x = np.copy(x)
    r = random.randint(0, len(x) -1)
    if random.random() > 0.1:
        x[r][0] += random.gauss(0, 36000)
    else:
        x[r][1] = random.randint(0, problem["number_ramps"] - 1)
    return x

Funktion zur Darstellung der Gantt Diagramme. Hier werden auch die Farben der Transportfahrzeuge festgesetzt und abgespeichert. 

In [24]:
def plot(schedule, number_of_ramps): 
    np.random.seed(42)
    ids = orders["id"].unique()
    colors_for_ids = [np.random.rand(3) for id in ids]
    
    fig, gnt = plt.subplots(dpi=200) 
    fig.subplots_adjust(bottom=0.25)
          
    gnt.set_xlabel('Zeit') 
    gnt.set_ylabel('Rampen') 

    gnt.set_yticks([int(15 + x * 10) for x in range(number_of_ramps)])
    gnt.set_yticklabels([str(x) for x in range(number_of_ramps)]) 

    plt.xticks(rotation=45)

    gnt.xaxis.set_major_formatter(ticker.FuncFormatter(lambda x, pos: dt.fromtimestamp(x).strftime("%d.%m %H Uhr")))

    gnt.grid(True) 

    for ramp in range(number_of_ramps):
        slots = schedule.loc[schedule["ramp"] == ramp]
        slots["color"] = slots["id"].map(lambda id: colors_for_ids[int(id)])
        gnt.broken_barh(slots[["timestamp", "duration"]].to_numpy(), (ramp*10 + 10, 9), facecolors=slots["color"].to_numpy())
    
    return fig, gnt

Die Wahrscheinlichkeit, dass eine schlechtere Lösung als die aktuelle Lösung im Simulated Annealing Algorithmus gewählt wird.

In [25]:
def probability(temp, diff): 
    p = np.exp(-(diff/temp))
    return p 

Simulated Annealing Algorithmus. Temperatur, stopcondition und alpha werden an die Funktion übergeben.

In [26]:
def simulated_annealing(f, stopcondition, x, temperature, alpha):
    iteration = 0
    while not stopcondition(iteration):
        iteration += 1
        x_new = mutation(x)
        diff = np.abs(f(x_new) - f(x))
        p = probability(temperature, diff)

        if f(x_new) <= f(x):
            x = x_new
            yield x, temperature, f(x)
        else:
            if random.random() < p:
                x = x_new
                yield x, temperature, f(x)
        
        temperature *= alpha


Anzeigen und erstellen des ersten Plans. Die Erstellung des Ablaufplan wird im GIF verdeutlicht, wobei weitere Informationen zu der genauen Belegung von den Zeitfenstern der Tabelle rechts entnommen werden können.

In [27]:
orders_processed = preprocess(orders, problem["number_ramps"])

for schedule in delay_fit(orders_processed, problem["number_ramps"]):
    fig, gnt = plot(schedule, problem["number_ramps"])
    live.figshow(fig, width= 37)
live.repeat(fps= 2)

newest_schedule = schedule.copy(deep=True)
newest_schedule = newest_schedule.astype('int32')
newest_schedule["timestamp"] = newest_schedule["timestamp"].astype("datetime64[s]")
newest_schedule["desired_timestamp"] = newest_schedule["desired_timestamp"].astype("datetime64[s]")
newest_schedule["endtimes"] = newest_schedule["endtimes"].astype("datetime64[s]")
newest_schedule["duration"] = newest_schedule["duration"]//60

newest_schedule

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

id           timestamp  duration  ...            endtimes ramp  slot_id
0   1 2020-07-27 08:30:20        60  ... 2020-07-27 09:30:20    0        0
1   0 2020-07-27 10:00:20        90  ... 2020-07-27 11:30:20    0        1
2   2 2020-07-27 10:00:20       120  ... 2020-07-27 12:00:20    1        2
3   3 2020-07-27 10:45:20       105  ... 2020-07-27 12:30:20    2        3
4   4 2020-07-27 12:40:20        82  ... 2020-07-27 14:02:20    2        4
5   5 2020-07-27 11:45:20       130  ... 2020-07-27 13:55:20    0        5
6   6 2020-07-27 12:45:20        90  ... 2020-07-27 14:15:20    1        6

[7 rows x 7 columns]

Optimierung des Plans mit der zuvor erwähnten Simulated Annealing Funktion. Temperatur, stopcondition (Iterationen) und alpha können hier verändert werden. Die Optimierung wird wieder als GIF und Tabelle verdeutlicht, wobei t die Temperatur und fitness den Fitnessfunktionswert abbildet.

In [28]:
encoded = encode(schedule)
figure = live.figure(width= 40)
fig, gnt = plot(schedule, problem["number_ramps"])
gnt.set_title(f"t = {np.round(150, 2)}, fitness = {np.round(fitness(encoded, schedule, orders_processed), 2)}")
figure.figshow(fig)

for result, temperature, fit in simulated_annealing(
        f=lambda x: fitness(x, schedule, orders_processed),
        stopcondition=lambda i: i > 900,
        x=encoded,
        temperature = 200,
        alpha = 0.99
    ):  
    decoded = decode(result, schedule)
    fig, gnt = plot(decoded, problem["number_ramps"])
    gnt.set_title(f"t = {np.round(temperature, 2)}, fitness = {np.round(fit, 2)}")
    figure.figshow(fig)
figure.repeat(fps= 5)

newest_schedule = decoded.copy(deep=True)
newest_schedule = newest_schedule.astype('int32')
newest_schedule["timestamp"] = newest_schedule["timestamp"].astype("datetime64[s]")
newest_schedule["desired_timestamp"] = newest_schedule["desired_timestamp"].astype("datetime64[s]")
newest_schedule["endtimes"] = newest_schedule["endtimes"].astype("datetime64[s]")
newest_schedule["duration"] = newest_schedule["duration"]//60

newest_schedule

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

id           timestamp  duration  ...            endtimes ramp  slot_id
0   1 2020-07-27 08:30:20        60  ... 2020-07-27 09:30:20    1        0
1   0 2020-07-27 10:00:20        90  ... 2020-07-27 11:30:20    0        1
2   2 2020-07-27 10:00:20       120  ... 2020-07-27 12:00:20    1        2
3   3 2020-07-27 10:45:20       105  ... 2020-07-27 12:30:20    2        3
4   4 2020-07-27 09:17:20        82  ... 2020-07-27 10:39:20    2        4
5   5 2020-07-27 11:45:20       130  ... 2020-07-27 13:55:20    0        5
6   6 2020-07-27 12:45:20        90  ... 2020-07-27 14:15:20    2        6

[7 rows x 7 columns]

Eine Liste mit den bisher gelöschten Rampen wird hier erstellt.

In [29]:
deleted_ramps = []
decoded = decoded.astype(float)

Berechnung der Fitnessfunktionsbewertung für jedes einzelne Zeitfenster.

In [30]:
def calc_scores(schedule):
    schedule['score'] = (schedule['timestamp'] - schedule['desired_timestamp']).abs()

Die Zeitfenster werden bestimmt, die mit dem neu einzuplanenden Zeitfenster im Konflikt stehen.

In [31]:
def overlap_ids_in_ramp(order, schedule, ramp):
    slots_for_ramp = schedule.loc[schedule["ramp"] == ramp]
    overlaps = np.array([slot_overlap(slot, order) for _, slot in slots_for_ramp.iterrows()])
    overlap_ids = np.arange(len(overlaps))[overlaps >= -600]
    overlap_ids = map(lambda id: slots_for_ramp.iloc[id]["slot_id"], overlap_ids)
    return list(overlap_ids)

##Die Planungsheuristik. 
Hier wird wenn möglich eine freie Rampe zum gewünschten Zeitpunkt gesucht. Falls alle Rampen belegt wird, werden die Fitnessfunktionsbewertungen verglichen. Dabei wird die Bewertung des neu einzuplanenden Zeitfensters **x** mit der Summe aller Zeitfenster **y** verglichen, die mit **x** überschneiden. Wenn **x** eine niedrigere Bewertung hat als **y**, wird es verschoben, ansonst müssen die Zeitfenster **y** verschoben werden.

In [32]:
def compare_slot(schedule, order):   

    ramp_overlaps = [max_overlap_in_ramp(order, schedule, ramp) for ramp in range(problem["number_ramps"])]

    if min(ramp_overlaps) <= -600: 
        best_ramp = np.random.choice(np.argwhere(np.array(ramp_overlaps) == np.array(ramp_overlaps).min())[0])
        return best_ramp, order

    else:
        overlap_ids = overlap_ids_in_ramp(order, schedule, order["ramp"])
        score_overlaps = sum([schedule.loc[schedule["slot_id"] == overlap_id]["score"].item() for overlap_id in overlap_ids])

        if score_overlaps > order["score"]:
            best_ramp = np.random.choice(np.argwhere(np.array(ramp_overlaps) == np.array(ramp_overlaps).min())[0])
            while max_overlap_in_ramp(order, schedule, best_ramp) > 0:
                overlap = max_overlap_in_ramp(order, schedule, best_ramp)      
                order["timestamp"] += overlap + 600
                order["endtimes"] = order["timestamp"] + order["duration"]
            
            return best_ramp, order

        else:
            for i, overlap_id in enumerate(overlap_ids):

                new_slot = schedule[schedule["slot_id"] == overlap_id].iloc[0]
                ramp_overlaps = [max_overlap_in_ramp(new_slot, schedule, ramp) for ramp in range(problem["number_ramps"])]

                best_ramp = np.random.choice(np.argwhere(np.array(ramp_overlaps) == np.array(ramp_overlaps).min())[0])
                while max_overlap_in_ramp(new_slot, schedule, best_ramp) > 0:
                    overlap = max_overlap_in_ramp(new_slot, schedule, best_ramp)      
                    new_slot["timestamp"] += overlap + 600
                    new_slot["endtimes"] = new_slot["timestamp"] + new_slot["duration"]
                
                schedule.iloc[overlap_id.astype(int)] = new_slot
           
            return best_ramp, order


Bei Ereignis *add_ramp* wird eine neue Rampe hinzugefügt. Eine Anzahl von Aufträgen werden dabei erneut auf die bestmögliche Rampe verbucht, wozu nun auch die neue Rampe gehören kann. Die Anzahl berechnet sich aus der Anzahl der Aufträge durch die Anzahl der Rampen. Für die Umplanung wird die zuvor vorgestellte Planungsheuristik genutz.

In [33]:
def add_ramp(decoded):
    problem["number_ramps"] += 1
    schedule = decoded.copy(deep=True)
    schedule.duration = schedule.duration.astype(int)
    schedule.ramp = schedule.ramp.astype(int)

    for i in range(int(len(schedule.index) / problem["number_ramps"])):
        calc_scores(schedule)

        index_order = schedule["score"].argmax()
        
        order = schedule.iloc[index_order]

        order["timestamp"] = order["desired_timestamp"]
        order["endtimes"] = order["desired_timestamp"] + order["duration"]

        best_ramp, order = compare_slot(schedule, order)
        order["ramp"] = best_ramp

        new_score = np.abs(order["timestamp"] - order["desired_timestamp"])
        if new_score < schedule.at[index_order, "score"]:
            schedule.iloc[index_order] = order
        else:
            break

    return schedule

*Maintainance* erstellt ein Zeitfenster, was alle anderen Fenster in diesem Zeitraum verschiebt. Maintainance Instanzen besitzen immer die ID -1 und werden nur duch das Löschen der Rampe entfernt.

In [34]:
def maintenance(start_time, end_time, maintained_ramp, new_schedule):
    calc_scores(new_schedule)
    new_schedule.loc[len(new_schedule.index)] = [-1, start_time, end_time - start_time, start_time, end_time, maintained_ramp, len(new_schedule.index), 0]
    new_schedule.astype(float)
    
    def switch_ramp(order):
        current_ramp = order["ramp"]
        if current_ramp == maintained_ramp:
            best_ramp, order = compare_slot(new_schedule, order)
            order["ramp"] = best_ramp

        return order

    for i in range(len(new_schedule.index)):
        if new_schedule.iloc[i]["timestamp"] > start_time and new_schedule.iloc[i]["timestamp"] < end_time:
            new_schedule.iloc[i] = switch_ramp(new_schedule.iloc[i])

        if new_schedule.iloc[i]["timestamp"] < start_time and new_schedule.iloc[i]["timestamp"] < end_time:
            new_schedule.iloc[i] = switch_ramp(new_schedule.iloc[i])

        if new_schedule.iloc[i]["timestamp"] > start_time and new_schedule.iloc[i]["timestamp"] > end_time:
            new_schedule.iloc[i] = switch_ramp(new_schedule.iloc[i])
    
    return new_schedule


Bei dem Ereignis *delete_ramp* wird eine Rampe aus dem Plan entfernt. Alle auf dieser Rampe sich befindenden Zeitfenster müssen neu verplant werden.

In [35]:
def delete_ramp(deleted_ramp, new_schedule2):
    new_schedule = new_schedule2.copy(deep=True)
    calc_scores(new_schedule)

    # Funktion um Maintainance Instanzen zu löschen, es wird überprüft ob ein Zeitfenster die ID -1 besitzt.
    new_schedule = new_schedule.drop(new_schedule[(new_schedule["ramp"] == deleted_ramp) & (new_schedule["id"] == -1)].index)
    
    def switch_ramp(order):
        current_ramp = order["ramp"]
        if current_ramp == deleted_ramp:
            best_ramp, order = compare_slot(new_schedule, order)
            order["ramp"] = best_ramp
        return order

    deleted_ramps.append(deleted_ramp)
    for i in range(len(new_schedule.index)):
        new_schedule.iloc[i] = switch_ramp(new_schedule.iloc[i])

    return new_schedule

Das Ereignis Zeitfenster hinzufügen nutzt die Planungsheuristik, um das neue Zeitfenster zuzuweisen.

In [36]:
def add_slot(new_schedule, start_time, duration, end_time, id):
    calc_scores(new_schedule)   
    
    new_schedule.loc[len(new_schedule.index)] = [id, start_time, duration, start_time, end_time, 2, len(new_schedule.index), 0]
    order = new_schedule.iloc[-1]
    best_ramp, order2 = compare_slot(new_schedule, order)
    order2["ramp"] = best_ramp

    return new_schedule


Das Ereignis *delete_slot* entfernt einfach das entsprechende Zeitfenster.

In [37]:
def delete_slot(new_schedule, slot_id):
    return new_schedule.drop(new_schedule[new_schedule["slot_id"] == slot_id].index)

Delay Slot verschiebt ein bereits existierendes Zeitfenster und nutzt dann die Planungsheuristik für die neue Einordnung. 

In [38]:
def delay_slot(new_schedule, index, delay):
    calc_scores(new_schedule)
    slot = new_schedule.iloc[index]

    slot["timestamp"] += delay
    slot["endtimes"] = slot["timestamp"] + slot["duration"]
    
    best_ramp, slot = compare_slot(new_schedule, slot)
    slot["ramp"] = best_ramp
    return new_schedule
    

Eine Ausgabe der Ereignisse in der Reihenfolge, in der sie ausgeführt werden. Die Ereignisse wurden zuvor basierend auf der mitgegebenen Ausführungszeit sortiert.

In [39]:
events_output = events.copy(deep=True)
events_output["timestamp"] = events_output["timestamp"].astype("datetime64[s]")
events_output

timestamp          type
4 2020-07-27 06:45:20    delay_slot
2 2020-07-27 10:00:20      add_ramp
5 2020-07-27 12:45:20    delay_slot
3 2020-07-27 14:45:20   delete_ramp
0 2020-07-28 10:00:20      add_slot
6 2020-07-28 12:00:20  maintainance
1 2020-07-28 14:00:20   delete_slot

Die *event_queue* soll die richtigen Funktionen basierend auf der *events* Tabelle ausführen. Dafür bekommt sie sequentiell alle event types aus dieser Tabelle übergeben.

In [40]:
def event_queue(new_schedule2, event_type):

        for type_added_ramps in range(len(preprocessed_added_ramps)):
            if events.iloc[event_type]["type"] == "add_ramp":
                new_schedule2 = add_ramp(new_schedule2)
                return new_schedule2
    
        for type_deleted_ramps in range(len(preprocessed_deleted_ramps)):
            if events.iloc[event_type]["type"] == "delete_ramp":
                new_schedule2 = delete_ramp(preprocessed_deleted_ramps.iloc[type_deleted_ramps]["ramp"], new_schedule2)
                return new_schedule2

        for type_added_slots in range(len(preprocessed_added_slots)):
            if events.iloc[event_type]["type"] == "add_slot":
                new_schedule2 = add_slot(new_schedule2, preprocessed_added_slots.iloc[type_added_slots]["timestamp_slot"],preprocessed_added_slots.iloc[type_added_slots]["duration"], preprocessed_added_slots.iloc[type_added_slots]["timestamp_slot"] + preprocessed_added_slots.iloc[type_added_slots]["duration"], preprocessed_added_slots.iloc[type_added_slots]["id"]) 
                return new_schedule2
                    
        for type_deleted_slots in range(len(preprocessed_deleted_slots)):
            if events.iloc[event_type]["type"] == "delete_slot":
                new_schedule2 = delete_slot(new_schedule2, preprocessed_deleted_slots.iloc[type_deleted_slots]["id"])
                return new_schedule2

        for type_delayed_slots in range(len(preprocessed_delayed_slots)):
            if events.iloc[event_type]["type"] == "delay_slot":
                new_schedule2 = delay_slot(new_schedule2, preprocessed_delayed_slots.iloc[type_delayed_slots]["id"], preprocessed_delayed_slots.iloc[type_delayed_slots]["delay"])
                return new_schedule2

        for type_maintainance in range(len(preprocessed_maintainance)):
            if events.iloc[event_type]["type"] == "maintainance":
                new_schedule2 = maintenance(preprocessed_maintainance.iloc[type_maintainance]["timestamp_slot"], preprocessed_maintainance.iloc[type_maintainance]["timestamp_slot"] + preprocessed_maintainance.iloc[type_maintainance]["duration"], preprocessed_maintainance.iloc[type_maintainance]["ramp"], new_schedule2)
                return new_schedule2


Die Event Tabelle wird durchlaufen, an *event_queue* übergeben und der erstellte Plan dargestellt, sowie der angepasste Plan in Tabellenform.

In [41]:
new_schedule2 = decoded

for event_type in range(len(events["type"])):
    new_schedule2 = event_queue(new_schedule2, event_type)
    fig, gnt = plot(new_schedule2, problem["number_ramps"])
    gnt.set_title(events["type"].iloc[event_type])
    live.figshow(fig, width= 40)
live.repeat(fps=0.5)

newest_schedule = new_schedule2.copy(deep=True)
newest_schedule = newest_schedule.astype('int32')
newest_schedule["timestamp"] = newest_schedule["timestamp"].astype("datetime64[s]")
newest_schedule["desired_timestamp"] = newest_schedule["desired_timestamp"].astype("datetime64[s]")
newest_schedule["endtimes"] = newest_schedule["endtimes"].astype("datetime64[s]")
newest_schedule["duration"] = newest_schedule["duration"]//60
newest_schedule["score"] = newest_schedule["score"]//60

newest_schedule


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

id           timestamp  duration  ... ramp slot_id  score
0   1 2020-07-27 08:30:20        60  ...    1       0      0
1   0 2020-07-27 15:35:20        90  ...    2       1    265
3   3 2020-07-27 10:45:20       105  ...    2       3      0
4   4 2020-07-27 10:00:20        82  ...    3       4      0
5   5 2020-07-27 14:15:20       130  ...    3       5    150
6   6 2020-07-27 12:45:20        90  ...    1       6      0
7   3 2020-07-27 14:30:20        60  ...    1       7      0
8  -1 2020-07-27 17:15:20       105  ...    1       8      0

[8 rows x 8 columns]

---------------------------------------------------------------------------------------